In [40]:
import pandas as pd
import polars as pl
import polars.selectors as cs
import numpy as np
import plotnine as pn
import plotly.graph_objs as go
import plotly.express as px
from tqdm.notebook import tqdm
from IPython.display import clear_output, display
import os
from itertools import product

from deap import base, creator, tools, algorithms
import imageio


%load_ext blackcellmagic

The blackcellmagic extension is already loaded. To reload it, use:
  %reload_ext blackcellmagic


In [120]:
def rastrigin(x, y):
    return 20 + (x**2 - 10 * np.cos(2 * np.pi * x)) + (y**2 - 10 * np.cos(2 * np.pi * y))

def ackley(x, y):
    return -20 * np.exp(-0.2 * np.sqrt(0.5 * (x**2 + y**2))) - np.exp(0.5 * (np.cos(2 * np.pi * x) + np.cos(2 * np.pi * y))) + 20 + np.e

def dropwave(x, y):
    numerator = - (1 + np.cos(12 * np.sqrt(x**2 + y**2)))
    denominator = 0.5 * (x**2 + y**2) + 2
    return numerator / denominator

def alpine02(x,y):  # vectorized form for plotting
    return -np.sqrt(x*y)*np.sin(x)*np.sin(y)

In [121]:
# Generate grid points for plotting
x_vals = np.linspace(-5, 5, 100)
y_vals = np.linspace(-5, 5, 100)
X, Y = np.meshgrid(x_vals, y_vals)

# Calculate function values for each grid point
Z_rastrigin = rastrigin(X, Y)
Z_ackley = ackley(X, Y)
Z_dropwave = dropwave(X, Y)
Z_alpine02 = alpine02(X, Y)

# Create Plotly surface plots
plots = [
    ('Rastrigin', X, Y, Z_rastrigin),
    ('Ackley', X, Y, Z_ackley),
    ('Dropwave', X, Y, Z_dropwave),
    ('Alpine02', X, Y, Z_alpine02),
]

for name, X, Y, Z in plots:
    fig = go.Figure(data=[go.Surface(z=Z, x=X, y=Y, colorscale="Blues")])
    fig.update_layout(
        width=600,
        height=600,
        showlegend=False
    )
    fig.write_image(f"{name}_3dplot.png", scale=2)
    fig.show()
    

C:\Users\mathi\AppData\Local\Temp\ipykernel_15156\2921452428.py:13: RuntimeWarning:

invalid value encountered in sqrt



In [43]:
for name, X, Y, Z in plots:
    fig = go.Figure(data=go.Contour(z=Z, x=x_vals, y=y_vals, colorscale="RdBu"))
    fig.update_layout(
        title=name + " Function Contour Plot", autosize=False, width=800, height=400
    )

    fig.add_trace(
        go.Scatter(x=[0], y=[0], mode="markers", marker=dict(size=10, color="red"))
    )
    fig.write_image(f"images/{name}.png", scale=2.5)
    fig.show()

### Using Genetic Algorithms with DEAP: Understanding the Library

Since the actual structure of the required individuals in genetic algorithms does strongly depend on the task at hand, DEAP does not contain any explicit structure. It will rather provide a convenient method for creating containers of attributes, associated with fitnesses, called the deap.creator. Using this method we can create custom individuals in a very simple way.

In [44]:
creator.create("FitnessMin", base.Fitness, weights=(-1.0,))
creator.create("Individual", list, fitness=creator.FitnessMin)

c:\Users\mathi\miniconda3\envs\general\Lib\site-packages\deap\creator.py:185: RuntimeWarning:

A class named 'FitnessMin' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.

c:\Users\mathi\miniconda3\envs\general\Lib\site-packages\deap\creator.py:185: RuntimeWarning:

A class named 'Individual' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.



The creator is a class factory that can build new classes at run-time. It will be called with first the desired name of the new class, second the base class it will inherit, and in addition any subsequent arguments you want to become attributes of your class.

In [45]:
ind_size = 2

All the objects we will use on our way, an individual, the population, as well as all functions, operators, and arguments will be stored in a DEAP container called Toolbox. It contains two methods for adding and removing content, register() and unregister().

In [46]:
toolbox = base.Toolbox()
# Attribute generator 
toolbox.register("attr_float", np.random.uniform, -5, 5)

Initialise a generation function that samples uniformly in the input space.

In [47]:
# Structure initializers
toolbox.register("individual", tools.initRepeat, creator.Individual, toolbox.attr_float, 2)
toolbox.register("population", tools.initRepeat, list, toolbox.individual)

In [48]:
# CXPB  is the probability with which two individuals
# are crossed
# MUTPB is the probability for mutating an individual
CXPB, MUTPB = 0.5, 0.1

In [49]:
# Set the evaluation function
def evalOneMin(individual):
    return rastrigin(individual[0], individual[1]), 

In [50]:
# Genetic Operators
toolbox.register("evaluate", evalOneMin)
toolbox.register("mate", tools.cxTwoPoint)
toolbox.register("mutate", tools.mutGaussian, mu=0, sigma=0.1, indpb=0.05)
toolbox.register("select", tools.selTournament, tournsize=5)

In [51]:
# Creating popluation
population = toolbox.population(n=50)
population[:10]

[[2.7702990338584987, -1.5709623590746071],
 [-2.6073630164636583, 1.4450776442122244],
 [-1.5060075054665631, 2.0925668056743945],
 [-3.1887412978038085, -0.801179015312707],
 [3.8704538099303747, -0.03218703018815283],
 [-0.06403462859108089, -0.3914765323476974],
 [-0.8186538461317809, -3.4503656511515315],
 [-4.074165472877698, -0.3652340672865604],
 [-1.1831309587654681, -1.3654450915438754],
 [-3.4894093735557394, -3.4476642977946783]]

In [52]:
# Variable keeping track of the number of generations
generation = 0
total_generations = 50
min_values = []
mean_values = []
max_values = []

# Begin the evolution
while generation < total_generations:
    
    # Select the next generation individuals
    offspring = toolbox.select(population, len(population))

    # Clone the selected individuals
    offspring = list(map(toolbox.clone, offspring))

    # Apply crossover and mutation on the offspring
    for child1, child2 in zip(offspring[::2], offspring[1::2]):
        if np.random.random() < CXPB:
            toolbox.mate(child1, child2)
            del child1.fitness.values
            del child2.fitness.values

    for mutant in offspring:
        if np.random.random() < MUTPB:
            toolbox.mutate(mutant)
            del mutant.fitness.values

    # Evaluate the individuals with an invalid fitness
    # Those are the ones that have been deleted
    invalid_ind = [ind for ind in offspring if not ind.fitness.valid]
    fitnesses = map(toolbox.evaluate, invalid_ind)
    for ind, fit in zip(invalid_ind, fitnesses):
        ind.fitness.values = fit

    # Keep score of values for evaluation after training
    fit = [ind.fitness.values[0] for ind in offspring]
    min_values.append(np.min(fit))
    mean_values.append(np.mean(fit))
    max_values.append(np.max(fit))

    # Overwrite the current population with the offspring    
    population[:] = offspring

    # Increment counter
    generation += 1
    # Print status
    if generation % 10 == 0:
        print(f"Generation {generation} done...")

Generation 10 done...
Generation 20 done...
Generation 30 done...
Generation 40 done...
Generation 50 done...


In [53]:
history = pd.DataFrame(
    {
        "generation": np.arange(1, len(mean_values) + 1),
        "min": min_values,
        "mean": mean_values,
        "max": max_values,
    }
).melt(id_vars="generation")

fig = px.line(data_frame=history, x="generation", y="value", color="variable")
fig.show()

### Implementing a Clean Version and Making Visualisations

Since the actual structure of the required individuals in genetic algorithms does strongly depend on the task at hand, DEAP does not contain any explicit structure. It will rather provide a convenient method for creating containers of attributes, associated with fitnesses, called the deap.creator. Using this method we can create custom individuals in a very simple way.

In [126]:
# Set the evaluation function
def evalOneMin(individual):
    return ackley(individual[0], individual[1]), 

In [133]:
# Set fixed variables
TOTAL_GENERATIONS = 80
INDIVIDUAL_SIZE = 2

config = {'CXPB': 0.25,
 'MUTPB': 0.05,
 'MUT_SD': 0.6,
 'MUT_IND_PB': 0.5,
 'TOURNAMENT_SIZE': 3,
 'POP_SIZE': 500}

# Objective Direction
creator.create("FitnessMin", base.Fitness, weights=(-1.0,))

# Invidiaul Structure
creator.create("Individual", list, fitness=creator.FitnessMin)

# Initialise the toolbox
toolbox = base.Toolbox()

# Attribute generator for individual genes
toolbox.register("attr_float", np.random.uniform, -4, -5)

# Structure initializers
toolbox.register(
    "individual",
    tools.initRepeat,
    creator.Individual,
    toolbox.attr_float,
    INDIVIDUAL_SIZE,
)
toolbox.register("population", tools.initRepeat, list, toolbox.individual)

# Genetic Operators
toolbox.register("evaluate", evalOneMin)
toolbox.register("mate", tools.cxOnePoint)
toolbox.register(
    "mutate",
    tools.mutGaussian,
    mu=0,
    sigma=config["MUT_SD"],
    indpb=config["MUT_IND_PB"],
)
toolbox.register("select", tools.selTournament, tournsize=config["TOURNAMENT_SIZE"])

# Creating the initial
population = toolbox.population(n=config["POP_SIZE"])

# Begin the evolution
generations = []
best_fitnesses = []

for generation in tqdm(range(TOTAL_GENERATIONS)):

    # Select the next generation individuals
    offspring = toolbox.select(population, len(population))

    # Clone the selected individuals
    offspring = list(map(toolbox.clone, offspring))

    # Apply crossover and mutation on the offspring
    for child1, child2 in zip(offspring[::2], offspring[1::2]):
        if np.random.random() < config["CXPB"]:
            toolbox.mate(child1, child2)
            del child1.fitness.values
            del child2.fitness.values

    for mutant in offspring:
        if np.random.random() < config["MUTPB"]:
            toolbox.mutate(mutant)
            del mutant.fitness.values

    # Evaluate the individuals with an invalid fitness
    # Those are the ones that have been deleted
    invalid_ind = [ind for ind in offspring if not ind.fitness.valid]
    fitnesses = map(toolbox.evaluate, invalid_ind)
    for ind, fit in zip(invalid_ind, fitnesses):
        ind.fitness.values = fit

    # Overwrite the current population with the offspring
    population[:] = offspring

    # Increment counter
    generation += 1

    # Get fitnesses
    fitnesses = [ind.fitness.values[0] for ind in population]
    fit_avg = np.mean(fitnesses)
    fit_best = np.min(fitnesses)

    # Get the best individual
    best_index = fitnesses.index(np.min(fitnesses))
    best_indiv = population[best_index]

    # Append the plot information
    generations.append(generation)
    best_fitnesses.append(fit_best)

    # Write the contour plot
    fig = go.Figure(data=[go.Contour(z=Z_ackley, x=x_vals, y=y_vals, 
                                     colorscale="Blues")])
    fig.add_trace(
        go.Scatter(
            x=[ind[0] for ind in population],
            y=[ind[1] for ind in population],
            mode="markers",
            marker=dict(size=3, color="black"),
        )
    )
    fig.add_trace(
        go.Scatter(
            x=[best_indiv[0]],
            y=[best_indiv[1]],
            mode="markers",
            line=dict(width=1, color="black"),
            marker=dict(size=8, color="firebrick"),
        )
    )
    fig.update_layout(
        width=600,
        height=600,
        showlegend=False
    )
    fig.update_xaxes(range=[-5, 5])
    fig.update_yaxes(range=[-5, 5])

    fig.write_image(f"ackley/{generation:04d}.png", scale=2)
    
    # Write the line plot
    fig = px.line(x=generations, y=best_fitnesses)
    fig.update_xaxes(range=[0, TOTAL_GENERATIONS])
    fig.update_layout(
            title=f"Generation: {generation} Best: {fit_best:.2f}",
            title_font=dict(size=28),
            title_x=0.5,
            xaxis_title="Generation",
            yaxis_title="Best Solution",
            width=1200,
            height=300,
            showlegend=False
        )

    fig.write_image(f"ackley_history/{generation:04d}.png", scale=2)

c:\Users\mathi\miniconda3\envs\general\Lib\site-packages\deap\creator.py:185: RuntimeWarning:

A class named 'FitnessMin' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.

c:\Users\mathi\miniconda3\envs\general\Lib\site-packages\deap\creator.py:185: RuntimeWarning:

A class named 'Individual' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.



  0%|          | 0/80 [00:00<?, ?it/s]

### Create a GIF from the PNGs

In [134]:
def generate_gif(folder_path, output_path):
    # Get list of PNG files sorted
    file_names = sorted([f for f in os.listdir(folder_path) if f.endswith('.png')])

    # Duration of each frame in seconds (assuming 20 frames per second)
    frame_duration = 1 / 20

    # List to store images
    images = []

    writer = imageio.get_writer(output_path, fps=10)
    # Read PNG files and append to images list
    for file_name in file_names:
        file_path = os.path.join(folder_path, file_name)
        im = imageio.imread(file_path)
        writer.append_data(im)

    writer.close()

In [135]:
# Ackley contour plot
generate_gif("ackley", "ackley_contour.mp4")

# Ackley history
generate_gif("ackley_history", "ackley_history.mp4")


C:\Users\mathi\AppData\Local\Temp\ipykernel_15156\139982273.py:15: DeprecationWarning:

Starting with ImageIO v3 the behavior of this function will switch to that of iio.v3.imread. To keep the current behavior (and make this warning disappear) use `import imageio.v2 as imageio` or call `imageio.v2.imread` directly.

IMAGEIO FFMPEG_WRITER WARNING: input image is not divisible by macro_block_size=16, resizing from (2400, 600) to (2400, 608) to ensure video compatibility with most codecs and players. To prevent resizing, make your input image divisible by the macro_block_size or set the macro_block_size to 1 (risking incompatibility).
